In [153]:
import math
from shapely.geometry import Point,Polygon
import folium
import pandas as pd
import geopandas as gpd
import requests
import os
from dotenv import load_dotenv
from sklearn.preprocessing import MinMaxScaler
import numpy as np
load_dotenv(".env")
from tqdm import tqdm
import json

from folium.plugins import HeatMap

In [154]:
# populartimes　の読み込み
with open("./data/populartimes.geojson", "r", encoding="utf-8") as f:
    populartimes = json.load(f)

populartimes = gpd.GeoDataFrame.from_features(populartimes["features"])

# 山口県のポリゴンを読み込み
yamaguchi_polygon = gpd.read_file("./yamaguchi-area/N03-19_35_190101.shp")
tokuyama_polygon = yamaguchi_polygon[yamaguchi_polygon["N03_007"] == "35215"]
tokuyama_polygon = tokuyama_polygon.unary_union
tokuyama_polygon

# 山口県の人口メッシュデータを読み込み
population = gpd.read_file("./data/tblT001101H5131.csv", encoding="shift-jis")
mesh = gpd.read_file("./data/HDDSWH5131/MESH05131.shp")
population = population.merge(mesh, on="KEY_CODE", how="left")
population["T001101001"] = pd.to_numeric(population["T001101001"], errors="coerce")
# MinMaxScalerのインスタンスを作成
scaler = MinMaxScaler()
population = population[["geometry", "T001101001"]]
population["normalized"] = scaler.fit_transform(population[["T001101001"]])

/tmp/ipykernel_48509/1061190204.py:10: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  tokuyama_polygon = tokuyama_polygon.unary_union


In [155]:
# foliumの地図を作成
center_lat = tokuyama_polygon.centroid.y
center_lon = tokuyama_polygon.centroid.x
m = folium.Map(location=[center_lat, center_lon], zoom_start=12)

# 人口メッシュデータを表示
for idx, row in population.iterrows():
    if row["geometry"] and pd.notnull(row["T001101001"]):
        # ポリゴンの座標を取得
        coordinates = list(row["geometry"].exterior.coords)
        # 緯度と経度を入れ替え
        coordinates = [(y, x) for x, y in coordinates]

        folium.Polygon(
            locations=coordinates,
            fill=True,
            fill_color="red",
            stroke=False,
            fill_opacity=row["normalized"] - 0.2,
        ).add_to(m)

In [158]:
# 飲み屋街インデックスのひょじ

column = "averaged_Monday"
time = "20-24"
time_series = ["0-4", "4-8", "8-12", "12-16", "16-20", "20-24"]
time_index = time_series.index(time)
data = []
for idx, row in populartimes.iterrows():
    if not row["geometry"].is_empty and row[column] is not None:
        # row[column]がNoneではなく、かつgeometryが空でない場合のみ処理
        data.append([row["geometry"].y, row["geometry"].x, row[column][time_index]])

HeatMap(data).add_to(m)

In [159]:
m